In [1]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from fit_tool.fit_file import FitFile
from fit_tool.profile.messages.record_message import RecordMessage
from fit_tool.profile.messages.file_id_message import FileIdMessage
import glob
import os


fitpath = r"D:\AZ\my docs\Sport\bike\Power comp\2023-02\19"
powercurve = {}

def read_data():
   
    os.chdir(fitpath)
    fit_data = {}
    
    for fitfile in glob.glob("*.fit"):

        if (fitfile + ".xlsx") in glob.glob("*.xlsx"):
            print(f"{fitfile}: Excel data found - loading from it")
            data = pd.read_excel(fitfile + ".xlsx", index_col=0)
        
        else:
            print(f"{fitfile}: Excel not found. Reading from FIT file.")

            app_fit = FitFile.from_file(fitfile)

            timestamp1 = []
            power1 = []
            distance1 = []
            speed1 = []
            cadence1 = []

            for record in app_fit.records:
                message = record.message
                if isinstance(message, RecordMessage):
                    timestamp1.append(message.timestamp)
                    #distance1.append(message.distance)
                    power1.append(message.power)
                    #speed1.append(message.speed)
                    cadence1.append(message.cadence)

            data = pd.DataFrame(data={"Time": pd.to_datetime(timestamp1, unit="ms"),
                                                    "Power": power1, 
                                                    "Cadence": cadence1})

            data["SMA10"] = data["Power"].rolling(10).mean()
            data["SMA3"] = data["Power"].rolling(3).mean()
            
            data.to_excel(fitfile + ".xlsx")
            print(f"{fitfile}: Data saved to Excel file.")
            
        fit_data[fitfile] = data

        print(f'{fitfile}: Data processing completed')
    
    return fit_data

def plot_data():
    ax1 = plt.subplot(311)
    ax1.plot(time1, power1, '-o', label='app [W]')
    ax1.legend(loc="upper right")
    plt.xlabel('Time (s)')
    plt.ylabel('Power (W)')

    plt.subplot(312, sharex=ax1)
    plt.plot(time1, speed1, '-o', label='app [m/s]')
    plt.legend(loc="upper right")
    plt.xlabel('Time (s)')
    plt.ylabel('speed (m/s)')

    plt.subplot(313, sharex=ax1)
    plt.plot(time1, cadence1, '-o', label='app [rpm]')
    plt.legend(loc="upper right")
    plt.xlabel('Time (s)')
    plt.ylabel('cadence (rpm)')

    plt.show()
    
    return

def plot_power_curve(data):
    powercurve_times = [("1s", 1),
                    ("5s", 5),
                    ("15s", 15),
                    ("1m", 60),
                    ("5m", 5*60),
                    ("10m", 10*60), 
                    ("20m", 20*60)]

    maxpower = {}
    meanpower = {}
    
    for point, duration in powercurve_times:
        maxpower[point] = data["Power"].rolling(duration).mean().max()
        meanpower[point] = data["Power"].rolling(duration).mean().mean()
        
    return maxpower, meanpower

def align_time(name1, name2):
    time_window_size = 60
    delta_map = {}
    offset = 0
    
    if pd.merge(fit_source_data[name1], fit_source_data[name2], on=["Time"]).empty:
        return 0
        
    for i in range(-time_window_size, time_window_size):
        offset_data = fit_source_data[name2].copy()
        offset_data["Time"] += pd.Timedelta(i,unit="s")
        
        merged_df = pd.merge(fit_source_data[name1], offset_data, on=["Time"])
        
        delta_map[i] = ((merged_df["Power_x"] - merged_df["Power_y"]) ** 2).mean()

        #print(delta_map[i])
        
        if (i == -time_window_size) or (delta_map[i] < min_delta):
            min_delta = delta_map[i]
            time_delta = i
            aligned_df = merged_df
        
    print(f"Delta: {time_delta} sec")
        
    return aligned_df

In [ ]:
fit_source_data = read_data()

In [ ]:
fix, axs = plt.subplots(2,1)

powercurve_max = {}
powercurve_mean = {}

x = sorted(fit_source_data.keys())
for i in range(len(x)):
    powercurve_max[x[i]], powercurve_mean[x[i]] = plot_power_curve(fit_source_data[x[i]])
    
    for j in range(i+1,len(x)):
        merged_df = align_time(x[i], x[j])
        if not merged_df.empty:
            merged_df.to_excel(f"{x[i]} vs {x[j]}_aligned.xlsx")
            
            axs[0].plot(merged_df.Time, merged_df.SMA10_x)
            axs[0].plot(merged_df.Time, merged_df.SMA10_y)

powercurve_mean_df = pd.DataFrame(powercurve_mean)
powercurve_max_df = pd.DataFrame(powercurve_mean)
            
for column in powercurve_mean_df.columns:
    axs[1].plot(powercurve_mean_df.index, powercurve_mean_df[column])

In [ ]:
powercurve_mean_df.iloc[:,0] - powercurve_mean_df.iloc[:,1]

In [10]:
from fitparse import FitFile

os.chdir(fitpath)
fit_data = {}

for file in glob.glob("*.fit"):

    fitfile = FitFile(file)
    data_df = []

    # Get all data messages that are of type record
    for record in fitfile.get_messages('record'):

        for power in record:
            print(power)


altitude: 18.0 [m]
cadence: 34 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 2.16 [m]
distance: None [m]
enhanced_altitude: 18.0 [m]
enhanced_speed: 2.235 [m/s]
grade: None [%]
heart_rate: 64 [bpm]
position_lat: 614530687 [semicircles]
position_long: -930548 [semicircles]
power: 143 [watts]
resistance: None
speed: None [m/s]
speed: 2.235 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:07:29
altitude: 18.0 [m]
cadence: 49 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 4.89 [m]
distance: None [m]
enhanced_altitude: 18.0 [m]
enhanced_speed: 3.163 [m/s]
grade: None [%]
heart_rate: 64 [bpm]
position_lat: 614530743 [semicircles]
position_long: -931005 [semicircles]
power: 180 [watts]
resistance: None
speed: None [m/s]
speed: 3.163 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:07:30
altitude: 18.0 [m]
cadence: 57 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distan

temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:08:48
altitude: 21.200000000000045 [m]
cadence: 86 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 451.61 [m]
distance: None [m]
enhanced_altitude: 21.200000000000045 [m]
enhanced_speed: 4.93 [m/s]
grade: None [%]
heart_rate: 105 [bpm]
position_lat: 614529202 [semicircles]
position_long: -1003925 [semicircles]
power: 78 [watts]
resistance: None
speed: None [m/s]
speed: 4.93 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:08:49
altitude: 21.200000000000045 [m]
cadence: 86 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 456.43 [m]
distance: None [m]
enhanced_altitude: 21.200000000000045 [m]
enhanced_speed: 4.683 [m/s]
grade: None [%]
heart_rate: 105 [bpm]
position_lat: 614529301 [semicircles]
position_long: -1004740 [semicircles]
power: 25 [watts]
resistance: None
speed: None [m/s]
speed: 4.683 [m/s]
temperature: None [C]
time_from_course

distance: 776.41 [m]
distance: None [m]
enhanced_altitude: 25.200000000000045 [m]
enhanced_speed: 7.828 [m/s]
grade: None [%]
heart_rate: 108 [bpm]
position_lat: 614537007 [semicircles]
position_long: -1058191 [semicircles]
power: 129 [watts]
resistance: None
speed: None [m/s]
speed: 7.828 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:10:06
altitude: 25.600000000000023 [m]
cadence: 87 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 784.02 [m]
distance: None [m]
enhanced_altitude: 25.600000000000023 [m]
enhanced_speed: 7.389 [m/s]
grade: None [%]
heart_rate: 108 [bpm]
position_lat: 614537336 [semicircles]
position_long: -1059388 [semicircles]
power: 129 [watts]
resistance: None
speed: None [m/s]
speed: 7.389 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:10:07
altitude: 26.0 [m]
cadence: 88 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 791.18 [m]
distance: None [m]
enhanced

position_lat: 614552474 [semicircles]
position_long: -1169591 [semicircles]
power: 158 [watts]
resistance: None
speed: None [m/s]
speed: 11.551 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:11:15
altitude: 16.600000000000023 [m]
cadence: 88 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 1457.4 [m]
distance: None [m]
enhanced_altitude: 16.600000000000023 [m]
enhanced_speed: 11.517 [m/s]
grade: None [%]
heart_rate: 118 [bpm]
position_lat: 614552502 [semicircles]
position_long: -1171573 [semicircles]
power: 160 [watts]
resistance: None
speed: None [m/s]
speed: 11.517 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:11:16
altitude: 16.399999999999977 [m]
cadence: 88 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 1468.91 [m]
distance: None [m]
enhanced_altitude: 16.399999999999977 [m]
enhanced_speed: 11.507 [m/s]
grade: None [%]
heart_rate: 117 [bpm]
position_lat: 614552534 [semi

timestamp: 2023-02-19 15:12:38
altitude: 14.799999999999955 [m]
cadence: 87 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 2293.58 [m]
distance: None [m]
enhanced_altitude: 14.799999999999955 [m]
enhanced_speed: 8.811 [m/s]
grade: None [%]
heart_rate: 127 [bpm]
position_lat: 614549867 [semicircles]
position_long: -1314599 [semicircles]
power: 198 [watts]
resistance: None
speed: None [m/s]
speed: 8.811 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:12:39
altitude: 14.799999999999955 [m]
cadence: 88 [rpm]
compressed_speed_distance: None
cycle_length: None [m]
distance: 2302.43 [m]
distance: None [m]
enhanced_altitude: 14.799999999999955 [m]
enhanced_speed: 8.877 [m/s]
grade: None [%]
heart_rate: 127 [bpm]
position_lat: 614549870 [semicircles]
position_long: -1316120 [semicircles]
power: 195 [watts]
resistance: None
speed: None [m/s]
speed: 8.877 [m/s]
temperature: None [C]
time_from_course: None [s]
timestamp: 2023-02-19 15:12:40
a

...

unknown_108: 2737
unknown_90: -3
accumulated_power: 997752 [watts]
cadence: 90 [rpm]
distance: 37250.22 [m]
enhanced_speed: 7.11 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 150 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 26.5 [percent]
left_power_phase: (331.87500518554697, 219.37500342773444) [degrees]
left_power_phase_peak: (57.65625090087892, 127.96875199951175) [degrees]
left_right_balance: 176
left_torque_effectiveness: 84.5 [percent]
power: 191 [watts]
resistance: 0
right_pco: 0 [mm]
right_pedal_smoothness: 29.0 [percent]
right_power_phase: (309.37500483398446, 233.437503647461) [degrees]
right_power_phase_peak: (59.06250092285158, 130.78125204345707) [degrees]
right_torque_effectiveness: 91.5 [percent]
speed: 7.11 [m/s]
temperature: 15 [C]
timestamp: 2023-02-19 16:32:31
unknown_108: 2573
unknown_90: -3
accumulated_power: 997935 [watts]
cadence: 91 [rpm]
distance: 37257.44 [m]
enhanced_speed: 7.213 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 150 [bpm]
left_pco: 0 [mm]
l

timestamp: 2023-02-19 16:33:30
unknown_108: 2899
unknown_90: -3
accumulated_power: 1008071 [watts]
cadence: 91 [rpm]
distance: 37682.84 [m]
enhanced_speed: 7.325 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 144 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 18.5 [percent]
left_power_phase: (336.0937552514649, 206.7187532299805) [degrees]
left_power_phase_peak: (60.46875094482424, 123.75000193359378) [degrees]
left_right_balance: 163
left_torque_effectiveness: 74.5 [percent]
power: 189 [watts]
resistance: 0
right_pco: 0 [mm]
right_pedal_smoothness: 30.0 [percent]
right_power_phase: (329.06250514160166, 208.1250032519532) [degrees]
right_power_phase_peak: (67.50000105468752, 130.78125204345707) [degrees]
right_torque_effectiveness: 90.5 [percent]
speed: 7.325 [m/s]
temperature: 15 [C]
timestamp: 2023-02-19 16:33:31
unknown_108: 3074
unknown_90: -3
accumulated_power: 1008244 [watts]
cadence: 93 [rpm]
distance: 37690.16 [m]
enhanced_speed: 7.325 [m/s]
fractional_cadence: 0.0 [rpm]
heart_

right_pedal_smoothness: 20.5 [percent]
right_power_phase: (341.71875533935554, 199.68750312011724) [degrees]
right_power_phase_peak: (67.50000105468752, 125.15625195556643) [degrees]
right_torque_effectiveness: 74.5 [percent]
speed: 6.867 [m/s]
temperature: 15 [C]
timestamp: 2023-02-19 16:34:24
unknown_108: 2747
unknown_90: -3
accumulated_power: 1015827 [watts]
cadence: 85 [rpm]
distance: 38054.67 [m]
enhanced_speed: 6.867 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 139 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 21.0 [percent]
left_power_phase: (343.1250053613282, 195.46875305419925) [degrees]
left_power_phase_peak: (60.46875094482424, 118.12500184570315) [degrees]
left_right_balance: 177
left_torque_effectiveness: 72.0 [percent]
power: 125 [watts]
resistance: 0
right_pco: 0 [mm]
right_pedal_smoothness: 17.0 [percent]
right_power_phase: (344.53125538330085, 196.87500307617194) [degrees]
right_power_phase_peak: (73.12500114257814, 126.5625019775391) [degrees]
right_torque_effecti

distance: 38481.87 [m]
enhanced_speed: 6.877 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 129 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 20.5 [percent]
left_power_phase: (336.0937552514649, 202.50000316406255) [degrees]
left_power_phase_peak: (64.68750101074221, 125.15625195556643) [degrees]
left_right_balance: 178
left_torque_effectiveness: 67.0 [percent]
power: 118 [watts]
resistance: 0
right_pco: 0 [mm]
right_pedal_smoothness: 19.0 [percent]
right_power_phase: (350.1562554711915, 208.1250032519532) [degrees]
right_power_phase_peak: (67.50000105468752, 125.15625195556643) [degrees]
right_torque_effectiveness: 66.0 [percent]
speed: 6.877 [m/s]
temperature: 15 [C]
timestamp: 2023-02-19 16:35:27
unknown_108: 2302
unknown_90: -3
accumulated_power: 1023730 [watts]
cadence: 87 [rpm]
distance: 38488.8 [m]
enhanced_speed: 6.923 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 128 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 21.5 [percent]
left_power_phase: (341.71875533935554, 203.9062

heart_rate: 123 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 24.0 [percent]
left_power_phase: (344.53125538330085, 203.9062531860352) [degrees]
left_power_phase_peak: (67.50000105468752, 123.75000193359378) [degrees]
left_right_balance: 173
left_torque_effectiveness: 77.5 [percent]
power: 90 [watts]
resistance: 0
right_pco: 0 [mm]
right_pedal_smoothness: 18.5 [percent]
right_power_phase: (0.0, 208.1250032519532) [degrees]
right_power_phase_peak: (66.09375103271486, 123.75000193359378) [degrees]
right_torque_effectiveness: 66.0 [percent]
speed: 6.765 [m/s]
temperature: 15 [C]
timestamp: 2023-02-19 16:36:22
unknown_108: 2222
unknown_90: -3
accumulated_power: 1029217 [watts]
cadence: 85 [rpm]
distance: 38861.95 [m]
enhanced_speed: 6.718 [m/s]
fractional_cadence: 0.0 [rpm]
heart_rate: 122 [bpm]
left_pco: 0 [mm]
left_pedal_smoothness: 19.0 [percent]
left_power_phase: (344.53125538330085, 203.9062531860352) [degrees]
left_power_phase_peak: (67.50000105468752, 123.75000193359378) [degrees]
l